In [3]:
import os

import tensorflow as tf
from tensorflow import keras
from tensorflow.keras.layers.experimental import preprocessing

import numpy as np
import os
import time

In [4]:
path_to_file = tf.keras.utils.get_file('shakespeare.txt', 'https://storage.googleapis.com/download.tensorflow.org/data/shakespeare.txt')

1122304/1115394 [==============================] - 0s 0us/step


In [5]:
# Read, then decode for py2 compat.
text = open(path_to_file, 'rb').read().decode(encoding='utf-8')
# The unique characters in the file
vocab = sorted(set(text))
ids_from_chars = preprocessing.StringLookup(
    vocabulary=list(vocab))
chars_from_ids = tf.keras.layers.experimental.preprocessing.StringLookup(
    vocabulary=ids_from_chars.get_vocabulary(), invert=True)

In [6]:
def text_from_ids(ids):
  return tf.strings.reduce_join(chars_from_ids(ids), axis=-1)

In [7]:
all_ids = ids_from_chars(tf.strings.unicode_split(text, 'UTF-8'))
ids_dataset = tf.data.Dataset.from_tensor_slices(all_ids)
seq_length = 100
examples_per_epoch = len(text)//(seq_length+1)

In [8]:
sequences = ids_dataset.batch(seq_length+1, drop_remainder=True)
def split_input_target(sequence):
    input_text = sequence[:-1]
    target_text = sequence[1:]
    return input_text, target_text

In [9]:
dataset = sequences.map(split_input_target)

In [10]:
# Batch size
BATCH_SIZE = 64

# Buffer size to shuffle the dataset
# (TF data is designed to work with possibly infinite sequences,
# so it doesn't attempt to shuffle the entire sequence in memory. Instead,
# it maintains a buffer in which it shuffles elements).
BUFFER_SIZE = 10000

dataset = (
    dataset
    .shuffle(BUFFER_SIZE)
    .batch(BATCH_SIZE, drop_remainder=True)
    .prefetch(tf.data.experimental.AUTOTUNE))

dataset

<PrefetchDataset shapes: ((64, 100), (64, 100)), types: (tf.int64, tf.int64)>

In [11]:
# Length of the vocabulary in chars
vocab_size = len(vocab)

# The embedding dimension
embedding_dim = 256

# Number of RNN units
rnn_units = 1024

In [12]:
class MyModel(tf.keras.Model):
  def __init__(self, vocab_size, embedding_dim, rnn_units):
    super().__init__(self)
    self.embedding = tf.keras.layers.Embedding(vocab_size, embedding_dim)
    self.gru = tf.keras.layers.GRU(rnn_units,
                                   return_sequences=True, 
                                   return_state=True)
    self.dense = tf.keras.layers.Dense(vocab_size)

  def call(self, inputs, states=None, return_state=False, training=False):
    x = inputs
    x = self.embedding(x, training=training)
    if states is None:
      states = self.gru.get_initial_state(x)
    x, states = self.gru(x, initial_state=states, training=training)
    x = self.dense(x, training=training)

    if return_state:
      return x, states
    else: 
      return x

In [13]:
model = MyModel(
    # Be sure the vocabulary size matches the `StringLookup` layers.
    vocab_size=len(ids_from_chars.get_vocabulary()),
    embedding_dim=embedding_dim,
    rnn_units=rnn_units)

In [15]:
for input_example_batch, target_example_batch in dataset.take(1):
    example_batch_predictions = model(input_example_batch)
    print(example_batch_predictions.shape, "# (batch_size, sequence_length, vocab_size)")
model.summary()

(64, 100, 67) # (batch_size, sequence_length, vocab_size)
Model: "my_model"
_________________________________________________________________
Layer (type)                 Output Shape              Param #   
embedding (Embedding)        multiple                  17152     
_________________________________________________________________
gru (GRU)                    multiple                  3938304   
_________________________________________________________________
dense (Dense)                multiple                  68675     
Total params: 4,024,131
Trainable params: 4,024,131
Non-trainable params: 0
_________________________________________________________________


In [28]:
# Restore the weights
latest = tf.train.latest_checkpoint('./checkpoints/')
latest

'./checkpoints/ckpt_29'

In [29]:
model.load_weights(latest)

In [30]:
class OneStep(tf.keras.Model):
  def __init__(self, model, chars_from_ids, ids_from_chars, temperature=1.0):
    super().__init__()
    self.temperature=temperature
    self.model = model
    self.chars_from_ids = chars_from_ids
    self.ids_from_chars = ids_from_chars

    # Create a mask to prevent "" or "[UNK]" from being generated.
    skip_ids = self.ids_from_chars(['','[UNK]'])[:, None]
    sparse_mask = tf.SparseTensor(
        # Put a -inf at each bad index.
        values=[-float('inf')]*len(skip_ids),
        indices = skip_ids,
        # Match the shape to the vocabulary
        dense_shape=[len(ids_from_chars.get_vocabulary())]) 
    self.prediction_mask = tf.sparse.to_dense(sparse_mask)

  @tf.function
  def generate_one_step(self, inputs, states=None):
    # Convert strings to token IDs.
    input_chars = tf.strings.unicode_split(inputs, 'UTF-8')
    input_ids = self.ids_from_chars(input_chars).to_tensor()

    # Run the model.
    # predicted_logits.shape is [batch, char, next_char_logits] 
    predicted_logits, states =  self.model(inputs=input_ids, states=states, 
                                          return_state=True)
    # Only use the last prediction.
    predicted_logits = predicted_logits[:, -1, :]
    predicted_logits = predicted_logits/self.temperature
    # Apply the prediction mask: prevent "" or "[UNK]" from being generated.
    predicted_logits = predicted_logits + self.prediction_mask

    # Sample the output logits to generate token IDs.
    predicted_ids = tf.random.categorical(predicted_logits, num_samples=1)
    predicted_ids = tf.squeeze(predicted_ids, axis=-1)

    # Convert from token ids to characters
    predicted_chars = self.chars_from_ids(predicted_ids)

    # Return the characters and model state.
    return predicted_chars, states

In [36]:
one_step_model = OneStep(model, chars_from_ids, ids_from_chars)

In [37]:
start = time.time()
states = None
next_char = tf.constant(['ROMEO:'])
result = [next_char]

for n in range(1000):
  next_char, states = one_step_model.generate_one_step(next_char, states=states)
  result.append(next_char)

result = tf.strings.join(result)
end = time.time()

print(result[0].numpy().decode('utf-8'), '\n\n' + '_'*80)

print(f"\nRun time: {end - start}")

ROMEO:
The more of day that I recreed
Her father's hand and unproved breathing senses.
I am not in a heart, cries 'furzedly and fully pleasure,
I should wake uponce to speak the issue not
sometime in Articians? Take my defianced
Cheer maker off the breath of blood.
She is too much more strange to keep his father with
him: let him sleep and joing to anger:
lay thee heir and many to death's son,
Doth glad my brother's love, and my sweet son,
The only son of Buckingham and Richmonds,
Below their faith resigns and holdsyman did not
I'll grace thee, if you kiss his writing wiltly,
Sweet Oxford, and the blood have of her
To present his shame, like so treeming and renowned law,
Served with her beauty's wange here or man
Which sometimes more behond to ere he had
let's past maintain'd with overbears;
Our Earl of Westminster, and I
Abtolice you for a harb, nurse,
I speak or sound so fair a other;
And when I met of, make pound us in Rome.

SEBASTIAN:
No, my good Lord; how fares me master,
And the

In [33]:
tf.saved_model.save(one_step_model, 'one_step')
one_step_reloaded = tf.saved_model.load('one_step')

INFO:tensorflow:Assets written to: one_step/assets


INFO:tensorflow:Assets written to: one_step/assets


In [34]:
states = None
next_char = tf.constant(['ROMEO:'])
result = [next_char]

for n in range(100):
  next_char, states = one_step_reloaded.generate_one_step(next_char, states=states)
  result.append(next_char)

print(tf.strings.join(result)[0].numpy().decode("utf-8"))

ROMEO:
The matter? what an unacknow art thou his hands?

GLOUCESTER:
Come, we'll leave her soul that Romeo


In [1]:
import tensorflow as tf

In [2]:
one_step_reloaded = tf.saved_model.load('one_step')

In [4]:
states = None
next_char = tf.constant(['to be'])
result = [next_char]

for n in range(100):
  next_char, states = one_step_reloaded.generate_one_step(next_char, states=states)
  result.append(next_char)

print(tf.strings.join(result)[0].numpy().decode("utf-8"))

to be abjuded me;
But, I ak they known more uncles blues,
To walk and fear him be as gone indone a past,



In [1]:
import numpy
from keras.models import Sequential
from keras.layers import Dense
from keras.layers import Dropout
from keras.layers import LSTM
from keras.callbacks import ModelCheckpoint
from keras.utils import np_utils

In [10]:
playfulltxt = ""
file = open("./shakestxts/cleantxts/eachLinePlay.txt", "r")
for line in file.readlines():
    code, actnum, scnum, speaker, linerange, content = line.split(",",5)
    playfulltxt += (" "+content[:-1].strip().replace(u'\xa0', u' '))

In [14]:
playfulltxt.casefold()

' enter king richard, john of gaunt, with other nobles and attendants. old john of gaunt, time-honored lancaster, hast thou, according to thy oath and band, brought hither henry hereford, thy bold son, here to make good the boist’rous late appeal, which then our leisure would not let us hear, against the duke of norfolk, thomas mowbray? i have, my liege. tell me, moreover, hast thou sounded him if he appeal the duke on ancient malice or worthily, as a good subject should, on some known ground of treachery in him? as near as i could sift him on that argument, on some apparent danger seen in him aimed at your highness, no inveterate malice. then call them to our presence. face to face and frowning brow to brow, ourselves will hear the accuser and the accusèd freely speak. high stomached are they both and full of ire, in rage deaf as the sea, hasty as fire. enter bolingbroke and mowbray. many years of happy days befall my gracious sovereign, my most loving liege. each day still better oth

In [12]:
poemfulltxt = ""
file = open("./shakestxts/cleantxts/eachLinePoem.txt", "r")
for line in file.readlines():
    code, linenum, content = line.split(",",2)
    poemfulltxt += (" "+content[:-1].strip().replace(u'\xa0', u' '))

In [15]:
poemfulltxt.casefold()

' from the besiegèd ardea all in post, borne by the trustless wings of false desire, lust-breathèd tarquin leaves the roman host and to collatium bears the lightless fire which, in pale embers hid, lurks to aspire and girdle with embracing flames the waist of collatine’s fair love, lucrece the chaste. haply that name of “chaste” unhapp’ly set this bateless edge on his keen appetite when collatine unwisely did not let to praise the clear unmatchèd red and white which triumphed in that sky of his delight, where mortal stars, as bright as heaven’s beauties, with pure aspects did him peculiar duties. for he the night before, in tarquin’s tent, unlocked the treasure of his happy state, what priceless wealth the heavens had him lent in the possession of his beauteous mate, reck’ning his fortune at such high proud rate that kings might be espousèd to more fame, but king nor peer to such a peerless dame. o, happiness enjoyed but of a few, and, if possessed, as soon decayed and done as is the m

In [16]:
raw_text = playfulltxt.casefold() + " " + poemfulltxt.casefold()

In [17]:
chars = sorted(list(set(raw_text)))

In [19]:
char_to_int = dict((c, i) for i, c in enumerate(chars))

In [22]:
n_chars = len(raw_text)
n_vocab = len(chars)
print("Total Characters: ", n_chars)
print("Total Vocab: ", n_vocab)

Total Characters:  4670315
Total Vocab:  65


In [40]:
seq_length = 10
dataX = []
dataY = []
for i in range(0, n_chars - seq_length, 1):
    seq_in = raw_text[i:i + seq_length]
    seq_out = raw_text[i + seq_length]
    dataX.append([char_to_int[char] for char in seq_in])
    dataY.append(char_to_int[seq_out])
n_patterns = len(dataX)
print("Total Patterns: ", n_patterns)

Total Patterns:  4670305


In [41]:
# reshape X to be [samples, time steps, features]
X = numpy.reshape(dataX, (n_patterns, seq_length, 1))
# normalize
X = X / float(n_vocab)
# one hot encode the output variable
y = np_utils.to_categorical(dataY)

In [42]:
# define the LSTM model
model = Sequential()
model.add(LSTM(256, input_shape=(X.shape[1], X.shape[2])))
model.add(Dropout(0.2))
model.add(Dense(y.shape[1], activation='softmax'))
model.compile(loss='categorical_crossentropy', optimizer='adam')

In [43]:
# define the checkpoint
filepath="weights-improvement-{epoch:02d}-{loss:.4f}.hdf5"
checkpoint = ModelCheckpoint(filepath, monitor='loss', verbose=1, save_best_only=True, mode='min')
callbacks_list = [checkpoint]

In [29]:
# model.fit(X, y, epochs=20, batch_size=128, callbacks=callbacks_list)

In [44]:
filename = "weights-10-improvement-03-2.1243.hdf5"#"weights-improvement-03-2.1293.hdf5"
model.load_weights(filename)
model.compile(loss='categorical_crossentropy', optimizer='adam')

In [45]:
int_to_char = dict((i, c) for i, c in enumerate(chars))

In [47]:
import sys
# pick a random seed
start = numpy.random.randint(0, len(dataX)-1)
pattern = dataX[start]
print("Seed:")
print("\"", ''.join([int_to_char[value] for value in pattern]), "\"")
# generate characters
for i in range(100):
    x = numpy.reshape(pattern, (1, len(pattern), 1))
    x = x / float(n_vocab)
    prediction = model.predict(x, verbose=0)
    index = numpy.argmax(prediction)
    result = int_to_char[index]
    seq_in = [int_to_char[value] for value in pattern]
    sys.stdout.write(result)
    pattern.append(index)
    pattern = pattern[1:len(pattern)]
print("\nDone.")

Seed:
"  conceit a "
nd toe the soor oo the farlern of the soor oo the farlern of the soor oo the farlern of the soor oo 
Done.
